# Installations

In [ ]:
# !pip install soundfile
# !pip install torchaudio

In [ ]:
!nvidia-smi

/bin/bash: line 1: nvidia-smi: command not found


# Parameters


In [ ]:
working_sr = 16000

In [ ]:
import os
import soundfile as sf
import librosa
import numpy as np
import IPython.display as ipd
import torchaudio
import torch
import torch.nn as nn
from tqdm import tqdm

In [ ]:
device = 'cuda' if torch.cuda.is_available() else 'cpu'

In [ ]:
# original_songs_sr = 44100
# resampler = torchaudio.transforms.Resample(orig_freq=original_songs_sr, new_freq=working_sr)

# Load Data

In [ ]:
base_path = '/content/drive/MyDrive/Ofir/SoundProcessingFinalProject'
data_path = os.path.join(base_path, 'Data')
dataset_path = os.path.join(data_path, 'dataset_organized')

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


## Load Audio Songs- no need, processed saved in drive

In [ ]:
# songs_path = os.path.join(data_path, 'songs')
# accompaniment_path = os.path.join(data_path, 'songs/accompaniment')
# vocal_path = os.path.join(data_path, 'songs/vocal')

In [ ]:
# songs_pairs = []
# for filename in os.listdir(accompaniment_path):
#     if filename.endswith(".wav"):
#         accompaniment_file = os.path.join(accompaniment_path, filename)
#         vocal_file = os.path.join(vocal_path, filename)

#         if os.path.exists(vocal_file):
#             try:
#                 # Load accompaniment and vocal files with torchaudio
#                 y_acc, sr_acc = torchaudio.load(accompaniment_file)  # [channels, samples]
#                 y_voc, sr_voc = torchaudio.load(vocal_file)

#                 # Check if sample rates are the same
#                 if sr_acc != sr_voc:
#                     print(f"Skipping {filename}: Different sample rates.")
#                     continue
#                 print(f"Sample Rate: {sr_acc}")

#                 # Ensure mono (convert stereo to mono if necessary)
#                 if y_acc.shape[0] > 1:
#                     y_acc = torch.mean(y_acc, dim=0, keepdim=True)
#                 if y_voc.shape[0] > 1:
#                     y_voc = torch.mean(y_voc, dim=0, keepdim=True)

#                 # Check if lengths are the same
#                 if y_acc.shape[1] != y_voc.shape[1]:
#                     print(f"Skipping {filename}: Different lengths.")
#                     continue

#                 songs_pairs.append((accompaniment_file, vocal_file))

#             except Exception as e:
#                 print(f"Error processing {filename}: {e}")

# print(f"Found {len(songs_pairs)} matching pairs.")

In [ ]:
# # Choose a pair by index (e.g., the first pair)
# index_to_play = 0  #@param {type:"integer"}

# if 0 <= index_to_play < len(songs_pairs):
#     accompaniment_file, vocal_file = songs_pairs[index_to_play]

#     print(f"Playing accompaniment: {accompaniment_file}")
#     ipd.display(ipd.Audio(accompaniment_file))

#     print(f"Playing vocal: {vocal_file}")
#     ipd.display(ipd.Audio(vocal_file))
# else:
#     print(f"Invalid index. Please choose an index between 0 and {len(songs_pairs) - 1}")


## Load Speech - no need, processed saved in drive

In [ ]:
# libri_speech_path = os.path.join(data_path, 'speech/LibriSpeech')

In [ ]:
# # prompt: Load LibriSpeech as pairs (audio-file, and transcript) from drive. structure: folders that contains folders that contains text file with the transcript and audio files

# libri_speech_pairs = []
# for root, _, files in os.walk(libri_speech_path):
#   #get the file that ends with .txt
#   for file in files:
#       if file.endswith(".txt"):
#         try:
#           with open(os.path.join(root, file), 'r') as f:
#             all_transcripts = f.read().strip()
#           # each row formated as '<file_name> <transcript>'
#           # example:
#           # 1272-141231-0003 HIS INSTANT OF PANIC WAS FOLLOWED BY A SMALL SHARP BLOW HIGH ON HIS CHEST while
#           # <file_name> = 1272-141231-0003 ; <transcript> = HIS INSTANT OF PANIC WAS FOLLOWED BY A SMALL SHARP BLOW HIGH ON HIS CHEST
#           # Parse all_transcripts and then Load file_name and save it as pair with its transcript (the one in the same line)
#           for line in all_transcripts.split('\n'):
#             audio_file_name, transcript = line.split(' ', 1)
#             audio_file_path = os.path.join(root, audio_file_name) + '.flac'
#             # Load the audio file
#             audio_file, sr = torchaudio.load(audio_file_path)
#             libri_speech_pairs.append((audio_file, transcript))
#         except Exception as e:
#           print(f"Error reading transcript for {line}: {e}")

# print(f"Found {len(libri_speech_pairs)} LibriSpeech pairs.")

In [ ]:
# # Example: Accessing the first pair
# if libri_speech_pairs:
#     audio_file, transcript = libri_speech_pairs[0]
#     print(f"Playing speech: {audio_file}")
#     ipd.display(ipd.Audio(audio_file, rate=sr))
#     print(f"Transcript: {transcript}")
# else:
#     print("No pairs found in libri_speech_pairs.")


# Prepare Data

In [ ]:
# spectogram parameters - currently by MelGAN
hop_length = 256
n_mels = 80
n_fft = 1024
sr = working_sr

## Mel Spectogram

In [ ]:
mel_transform  = torchaudio.transforms.MelSpectrogram(
    sample_rate=sr,
    n_fft=n_fft,
    win_length=n_fft,
    hop_length=hop_length,
    n_mels=n_mels,
).to(device)

def convert_waveform_to_mel_spectrogram(waveform):
    # Convert waveform to Mel spectrogram
    padded_waveform = torch.nn.functional.pad(waveform, (0, n_fft - waveform.size(1) % hop_length))
    mel_spectrogram = mel_transform(padded_waveform)  # Shape: [1, n_mels, time_steps]
    return mel_spectrogram

def slice_spectogram(mel_spectrogram, slice_duration):
  '''
  slice the spectogram into slices of the given duration, return list of slices
  '''
  samples_per_slice = int(sr * slice_duration / hop_length)  # Time steps per slice
  # Slice the spectrogram
  num_slices = mel_spectrogram.shape[2] // samples_per_slice
  slices = [mel_spectrogram[:, :, i * samples_per_slice:(i + 1) * samples_per_slice] for i in range(num_slices)]
  # convert slices to tensor
  slices = torch.stack(slices)

  return slices

### Data Helpers

In [ ]:
# prompt: take 2 pytorch mel spectograms batches, items in the batch are at the same length and combine items at the same index into one (like adding another audio channel- output: batch of mel spectogram at the same length that represent the original audio)

def combine_mel_spectrograms(batch1, batch2):
    """
    Combines two batches of mel spectrograms element-wise.

    Args:
        batch1: A batch of mel spectrograms (Tensor). Shape: (batch_size, n_mels, time_steps)
        batch2: A batch of mel spectrograms (Tensor). Shape: (batch_size, n_mels, time_steps)

    Returns:
        A combined batch of mel spectrograms (Tensor). Shape: (batch_size, 2, n_mels, time_steps)
    """

    # Check if input batches have the same dimensions
    if batch1.shape != batch2.shape:
        raise ValueError("Input batches must have the same dimensions.")

    # Combine the batches items
    combined_batch = batch1 + batch2
    return combined_batch


In [ ]:
# prompt: convert tensor mel-spectogram back to audio

import torch
import torchaudio

def convert_mel_to_audio(mel_spectrogram):
    """Converts a mel spectrogram back to an audio waveform.

    Args:
        mel_spectrogram: The mel spectrogram (torch.Tensor).

    Returns:
        The reconstructed audio waveform (torch.Tensor).
    """

    # Create an inverse mel spectrogram transform
    inverse_mel_transform = torchaudio.transforms.InverseMelScale(
        n_stft=n_fft // 2 + 1, n_mels=n_mels, sample_rate=sr
    )

    # Apply the inverse mel scale transform
    spectrogram = inverse_mel_transform(mel_spectrogram)

    # Create Griffin-Lim transform
    griffin_lim = torchaudio.transforms.GriffinLim(
        n_fft=n_fft, hop_length=hop_length
    )

    # Apply Griffin-Lim to reconstruct the waveform
    waveform = griffin_lim(spectrogram)
    return waveform


In [ ]:
def spectral_convergence(input, target):
    return 20 * ((input - target).norm().log10() - target.norm().log10())

def GRAD(spec, transform_fn, samples=None, init_x0=None, maxiter=1000, tol=1e-6, verbose=1, evaiter=10, lr=0.003):
    spec = torch.Tensor(spec)
    samples = (spec.shape[-1]*hop_length)-hop_length

    if init_x0 is None:
        init_x0 = spec.new_empty((1,samples)).normal_(std=1e-6)
    x = nn.Parameter(init_x0)
    T = spec

    criterion = nn.L1Loss()
    optimizer = torch.optim.Adam([x], lr=lr)

    bar_dict = {}
    metric_func = spectral_convergence
    bar_dict['spectral_convergence'] = 0
    metric = 'spectral_convergence'

    init_loss = None
    with tqdm(total=maxiter, disable=not verbose) as pbar:
        for i in range(maxiter):
            optimizer.zero_grad()
            V = transform_fn(x)
            loss = criterion(V, T)
            loss.backward()
            optimizer.step()
            lr = lr*0.9999
            for param_group in optimizer.param_groups:
              param_group['lr'] = lr

            if i % evaiter == evaiter - 1:
                with torch.no_grad():
                    V = transform_fn(x)
                    bar_dict[metric] = metric_func(V, spec).item()
                    l2_loss = criterion(V, spec).item()
                    pbar.set_postfix(**bar_dict, loss=l2_loss)
                    pbar.update(evaiter)

    return x.detach().view(-1).cpu()


### Convert Data- example- relay on the commented load data cells

In [ ]:
# # prompt: take songs pairs, convert to mel spectogram using the helpers functions above and convert back to audio and play it

# # Choose a pair by index
# index_to_play = 0  #@param {type:"integer"}

# if 0 <= index_to_play < len(songs_pairs):
#     accompaniment_file, vocal_file = songs_pairs[index_to_play]

#     # Load the accompaniment and vocal files
#     # y_acc, sr_acc = torchaudio.load(accompaniment_file)
#     y_voc, sr_voc = torchaudio.load(vocal_file)
#     y_voc = resampler(y_voc)
#     # Convert to mel spectrograms
#     # mel_acc = convert_waveform_to_mel_spectrogram(y_acc)
#     mel_voc = convert_waveform_to_mel_spectrogram(y_voc)
#     sliced = slice_spectogram(mel_voc, 10)[1]
#     # Combine the spectrograms (example: simple addition)
#     # combined_mel = combine_mel_spectrograms(mel_acc, mel_voc)

#     # Convert the combined spectrogram back to audio
#     reconstructed_audio = GRAD(sliced, mel_transform)

#     # Play the reconstructed audio
#     print("Playing reconstructed audio:")
#     ipd.display(ipd.Audio(reconstructed_audio.numpy(), rate=sr))
# else:
#     print(f"Invalid index. Please choose an index between 0 and {len(songs_pairs) - 1}")


# Model

In [ ]:
conv_dim = n_mels
d_conv_dim = 2 * conv_dim
k_common_size = 100
spec_norm = lambda x:  torch.nn.utils.spectral_norm(x) #Spectral normalization is a technique used to stabilize the training of GANs by controlling the Lipschitz constant of the layers.


In [ ]:
# UTILS
import glob
import os
import matplotlib
import torch
from torch.nn.utils import weight_norm
matplotlib.use("Agg")
import matplotlib.pylab as plt


def plot_spectrogram(spectrogram):
    fig, ax = plt.subplots(figsize=(10, 2))
    im = ax.imshow(spectrogram, aspect="auto", origin="lower",
                   interpolation='none')
    plt.colorbar(im, ax=ax)

    fig.canvas.draw()
    plt.close()

    return fig


def init_weights(m, mean=0.0, std=0.01):
    classname = m.__class__.__name__
    if classname.find("Conv") != -1:
        m.weight.data.normal_(mean, std)


def apply_weight_norm(m):
    classname = m.__class__.__name__
    if classname.find("Conv") != -1:
        weight_norm(m)


def get_padding(kernel_size, dilation=1):
    return int((kernel_size*dilation - dilation)/2)


def load_checkpoint(filepath, device):
    assert os.path.isfile(filepath)
    print("Loading '{}'".format(filepath))
    checkpoint_dict = torch.load(filepath, map_location=device)
    print("Complete.")
    return checkpoint_dict


def save_checkpoint(filepath, obj):
    print("Saving checkpoint to {}".format(filepath))
    torch.save(obj, filepath)
    print("Complete.")


def scan_checkpoint(cp_dir, prefix):
    pattern = os.path.join(cp_dir, prefix + '????????')
    cp_list = glob.glob(pattern)
    if len(cp_list) == 0:
        return None
    return sorted(cp_list)[-1]



## Generators

In [ ]:
import torch
import torch.nn.functional as F
import torch.nn as nn
from torch.nn import Conv1d, ConvTranspose1d, AvgPool1d, Conv2d
from torch.nn.utils import weight_norm, remove_weight_norm, spectral_norm

LRELU_SLOPE = 0.1

class ResBlock1(torch.nn.Module):
    def __init__(self, h, channels, kernel_size=3, dilation=(1, 3, 5)):
        super(ResBlock1, self).__init__()
        self.h = h
        self.convs1 = nn.ModuleList([
            weight_norm(Conv1d(channels, channels, kernel_size, 1, dilation=dilation[0],
                               padding=get_padding(kernel_size, dilation[0]))),
            weight_norm(Conv1d(channels, channels, kernel_size, 1, dilation=dilation[1],
                               padding=get_padding(kernel_size, dilation[1]))),
            weight_norm(Conv1d(channels, channels, kernel_size, 1, dilation=dilation[2],
                               padding=get_padding(kernel_size, dilation[2])))
        ])
        self.convs1.apply(init_weights)

        self.convs2 = nn.ModuleList([
            weight_norm(Conv1d(channels, channels, kernel_size, 1, dilation=1,
                               padding=get_padding(kernel_size, 1))),
            weight_norm(Conv1d(channels, channels, kernel_size, 1, dilation=1,
                               padding=get_padding(kernel_size, 1))),
            weight_norm(Conv1d(channels, channels, kernel_size, 1, dilation=1,
                               padding=get_padding(kernel_size, 1)))
        ])
        self.convs2.apply(init_weights)

    def forward(self, x):
        for c1, c2 in zip(self.convs1, self.convs2):
            xt = F.leaky_relu(x, LRELU_SLOPE)
            xt = c1(xt)
            xt = F.leaky_relu(xt, LRELU_SLOPE)
            xt = c2(xt)
            x = xt + x
        return x

    def remove_weight_norm(self):
        for l in self.convs1:
            remove_weight_norm(l)
        for l in self.convs2:
            remove_weight_norm(l)


class ResBlock2(torch.nn.Module):
    def __init__(self, h, channels, kernel_size=3, dilation=(1, 3)):
        super(ResBlock2, self).__init__()
        self.h = h
        self.convs = nn.ModuleList([
            weight_norm(Conv1d(channels, channels, kernel_size, 1, dilation=dilation[0],
                               padding=get_padding(kernel_size, dilation[0]))),
            weight_norm(Conv1d(channels, channels, kernel_size, 1, dilation=dilation[1],
                               padding=get_padding(kernel_size, dilation[1])))
        ])
        self.convs.apply(init_weights)

    def forward(self, x):
        for c in self.convs:
            xt = F.leaky_relu(x, LRELU_SLOPE)
            xt = c(xt)
            x = xt + x
        return x

    def remove_weight_norm(self):
        for l in self.convs:
            remove_weight_norm(l)

In [ ]:
class Generator(torch.nn.Module):
    def __init__(self, h):
        super(Generator, self).__init__()
        self.h = h
        self.num_kernels = len(h['resblock_kernel_sizes'])
        self.num_upsamples = len(h['upsample_rates'])
        self.conv_pre = weight_norm(Conv1d(n_mels, h['upsample_initial_channel'], 7, 1, padding=3))
        resblock = ResBlock1 if h['resblock'] == '1' else ResBlock2

        self.ups = nn.ModuleList()
        for i, (u, k) in enumerate(zip(h['upsample_rates'], h['upsample_kernel_sizes'])):
            self.ups.append(weight_norm(
                ConvTranspose1d(h['upsample_initial_channel']//(2**i), h['upsample_initial_channel']//(2**(i+1)),
                                k, u, padding=(k-u)//2)))

        self.resblocks = nn.ModuleList()
        for i in range(len(self.ups)):
            ch = h['upsample_initial_channel']//(2**(i+1))
            for j, (k, d) in enumerate(zip(h['resblock_kernel_sizes'], h['resblock_dilation_sizes'])):
                self.resblocks.append(resblock(h, ch, k, d))

        self.conv_post = weight_norm(Conv1d(ch, 1, 7, 1, padding=3))
        self.ups.apply(init_weights)
        self.conv_post.apply(init_weights)

    def forward(self, x):
        x = self.conv_pre(x)
        # print('after conv_pre', x.shape)
        for i in range(self.num_upsamples):
            x = F.leaky_relu(x, LRELU_SLOPE)
            # print('after leaky_relu', x.shape)
            x = self.ups[i](x)
            # print('after up', x.shape)
            xs = None
            for j in range(self.num_kernels):
                if xs is None:
                    xs = self.resblocks[i*self.num_kernels+j](x)
                else:
                    xs += self.resblocks[i*self.num_kernels+j](x)
                # print(f"after resblocks_{j}", xs.shape)

            x = xs / self.num_kernels
            # print('after resblocks all', x.shape)
        x = F.leaky_relu(x)
        # print('after leaky_relu', x.shape)
        x = self.conv_post(x)
        # print('after conv_post', x.shape)
        x = torch.tanh(x)

        return x

    def remove_weight_norm(self):
        print('Removing weight norm...')
        for l in self.ups:
            remove_weight_norm(l)
        for l in self.resblocks:
            l.remove_weight_norm()
        remove_weight_norm(self.conv_pre)
        remove_weight_norm(self.conv_post)



## Discrimenator

In [ ]:
class DiscriminatorP(torch.nn.Module):
    def __init__(self, period, kernel_size=5, stride=3, use_spectral_norm=False):
        super(DiscriminatorP, self).__init__()
        self.period = period
        norm_f = weight_norm if use_spectral_norm == False else spectral_norm
        self.convs = nn.ModuleList([
            norm_f(Conv2d(1, 32, (kernel_size, 1), (stride, 1), padding=(get_padding(5, 1), 0))),
            norm_f(Conv2d(32, 128, (kernel_size, 1), (stride, 1), padding=(get_padding(5, 1), 0))),
            norm_f(Conv2d(128, 512, (kernel_size, 1), (stride, 1), padding=(get_padding(5, 1), 0))),
            norm_f(Conv2d(512, 1024, (kernel_size, 1), (stride, 1), padding=(get_padding(5, 1), 0))),
            norm_f(Conv2d(1024, 1024, (kernel_size, 1), 1, padding=(2, 0))),
        ])
        self.conv_post = norm_f(Conv2d(1024, 1, (3, 1), 1, padding=(1, 0)))

    def forward(self, x):
        fmap = []

        # 1d to 2d
        b, c, t = x.shape
        if t % self.period != 0: # pad first
            n_pad = self.period - (t % self.period)
            x = F.pad(x, (0, n_pad), "reflect")
            t = t + n_pad
        x = x.view(b, c, t // self.period, self.period)

        for l in self.convs:
            x = l(x)
            x = F.leaky_relu(x, LRELU_SLOPE)
            fmap.append(x)
        x = self.conv_post(x)
        fmap.append(x)
        x = torch.flatten(x, 1, -1)

        return x, fmap


class MultiPeriodDiscriminator(torch.nn.Module):
    def __init__(self):
        super(MultiPeriodDiscriminator, self).__init__()
        self.discriminators = nn.ModuleList([
            DiscriminatorP(2),
            DiscriminatorP(3),
            DiscriminatorP(5),
            DiscriminatorP(7),
            DiscriminatorP(11),
        ])

    def forward(self, y, y_hat):
        y_d_rs = []
        y_d_gs = []
        fmap_rs = []
        fmap_gs = []
        for i, d in enumerate(self.discriminators):
            y_d_r, fmap_r = d(y)
            y_d_g, fmap_g = d(y_hat)
            y_d_rs.append(y_d_r)
            fmap_rs.append(fmap_r)
            y_d_gs.append(y_d_g)
            fmap_gs.append(fmap_g)

        return y_d_rs, y_d_gs, fmap_rs, fmap_gs


class DiscriminatorS(torch.nn.Module):
    def __init__(self, use_spectral_norm=False):
        super(DiscriminatorS, self).__init__()
        norm_f = weight_norm if use_spectral_norm == False else spectral_norm
        self.convs = nn.ModuleList([
            norm_f(Conv1d(1, 128, 15, 1, padding=7)),
            norm_f(Conv1d(128, 128, 41, 2, groups=4, padding=20)),
            norm_f(Conv1d(128, 256, 41, 2, groups=16, padding=20)),
            norm_f(Conv1d(256, 512, 41, 4, groups=16, padding=20)),
            norm_f(Conv1d(512, 1024, 41, 4, groups=16, padding=20)),
            norm_f(Conv1d(1024, 1024, 41, 1, groups=16, padding=20)),
            norm_f(Conv1d(1024, 1024, 5, 1, padding=2)),
        ])
        self.conv_post = norm_f(Conv1d(1024, 1, 3, 1, padding=1))

    def forward(self, x):
        fmap = []
        for l in self.convs:
            x = l(x)
            x = F.leaky_relu(x, LRELU_SLOPE)
            fmap.append(x)
        x = self.conv_post(x)
        fmap.append(x)
        x = torch.flatten(x, 1, -1)

        return x, fmap


class MultiScaleDiscriminator(torch.nn.Module):
    def __init__(self):
        super(MultiScaleDiscriminator, self).__init__()
        self.discriminators = nn.ModuleList([
            DiscriminatorS(use_spectral_norm=True),
            DiscriminatorS(),
            DiscriminatorS(),
        ])
        self.meanpools = nn.ModuleList([
            AvgPool1d(4, 2, padding=2),
            AvgPool1d(4, 2, padding=2)
        ])

    def forward(self, y, y_hat):
        y_d_rs = []
        y_d_gs = []
        fmap_rs = []
        fmap_gs = []
        for i, d in enumerate(self.discriminators):
            if i != 0:
                y = self.meanpools[i-1](y)
                y_hat = self.meanpools[i-1](y_hat)
            y_d_r, fmap_r = d(y)
            y_d_g, fmap_g = d(y_hat)
            y_d_rs.append(y_d_r)
            fmap_rs.append(fmap_r)
            y_d_gs.append(y_d_g)
            fmap_gs.append(fmap_g)

        return y_d_rs, y_d_gs, fmap_rs, fmap_gs


## Losses

In [ ]:
def feature_loss(fmap_r, fmap_g):
    loss = 0
    for dr, dg in zip(fmap_r, fmap_g):
        for rl, gl in zip(dr, dg):
            loss += torch.mean(torch.abs(rl - gl))

    return loss*2


def discriminator_loss(disc_real_outputs, disc_generated_outputs):
    loss = 0
    r_losses = []
    g_losses = []
    for dr, dg in zip(disc_real_outputs, disc_generated_outputs):
        r_loss = torch.mean((1-dr)**2)
        g_loss = torch.mean(dg**2)
        loss += (r_loss + g_loss)
        r_losses.append(r_loss.item())
        g_losses.append(g_loss.item())

    return loss #, r_losses, g_losses


def generator_loss(disc_outputs):
    loss = 0
    gen_losses = []
    for dg in disc_outputs:
        l = torch.mean((1-dg)**2)
        gen_losses.append(l)
        loss += l

    return loss

In [ ]:
def mae(x,y):
  return torch.functional.F.l1_loss(x,y)

def mse(x,y):
  return torch.functional.F.l2_loss(x,y)

def d_loss_f(fake):
  return torch.mean(torch.relu(1 + fake))

def d_loss_r(real):
  return torch.mean(torch.relu(1 - real))

def g_loss_f(fake):
  return torch.mean(-fake)


## Network

In [ ]:
hparams = {
    "resblock": 1, #ResBlock1 if h.resblock == '1' else ResBlock2
    "batch_size": 16,
    "learning_rate": 0.0002,
    "adam_b1": 0.8,
    "adam_b2": 0.99,
    "lr_decay": 0.999,
    "seed": 1234,

    "upsample_rates": [8,8,2,2],
    "upsample_kernel_sizes": [16,16,4,4],
    "upsample_initial_channel": 512,
    "resblock_kernel_sizes": [3,7,11],
    "resblock_dilation_sizes": [[1,3,5], [1,3,5], [1,3,5]],

    "fmin": 0,
    "fmax": 8000,
    "fmax_for_loss": None,
}

In [ ]:
# Define the save path in Google Drive
save_path = os.path.join(base_path, 'saved_models', 'HifiGAN_similar_singing')  # Adjust the path as needed
os.makedirs(save_path, exist_ok=True)  # Create the directory if it doesn't exist
# Save models after each epoch
gen_speech2sing_save_path = os.path.join(save_path, f'gen_speech2sing_const.pth')
gen_preprocess_singing_save_path = os.path.join(save_path, f'gen_preprocess_singing_const.pth')
gen_sing2speech_save_path = os.path.join(save_path, f'gen_sing2speech_epoch_const.pth')
discrim_whole_mpd_save_path = os.path.join(save_path, f'discrim_whole_mpd_epoch_const.pth')
discrim_vocal_mpd_save_path = os.path.join(save_path, f'discrim_vocal_mpd_epoch_const.pth')
discrim_whole_msd_save_path = os.path.join(save_path, f'discrim_whole_msd_epoch_const.pth')
discrim_vocal_msd_save_path = os.path.join(save_path, f'discrim_vocal_msd_epoch_const.pth')

def save_models(gen_speech2sing, gen_sing2speech, gen_preprocess_singing, discrim_whole_mpd, discrim_vocal_mpd, discrim_whole_msd, discrim_vocal_msd):
  torch.save(gen_speech2sing.state_dict(), gen_speech2sing_save_path)
  torch.save(gen_sing2speech.state_dict(), gen_sing2speech_save_path)
  torch.save(gen_preprocess_singing.state_dict(), gen_preprocess_singing_save_path)
  torch.save(discrim_whole_mpd.state_dict(), discrim_whole_mpd_save_path)
  torch.save(discrim_vocal_mpd.state_dict(), discrim_vocal_mpd_save_path)
  torch.save(discrim_whole_msd.state_dict(), discrim_whole_msd_save_path)
  torch.save(discrim_vocal_msd.state_dict(), discrim_vocal_msd_save_path)


In [ ]:
import itertools
#Get models and optimizers
def get_networks(hparams):
  global Generator, MultiPeriodDiscriminator, MultiScaleDiscriminator
  gen_speech2sing = Generator(hparams).to(device)
  gen_sing2speech = Generator(hparams).to(device)
  gen_preprocess_singing = Generator(hparams).to(device)
  discrim_whole_mpd = MultiPeriodDiscriminator().to(device)
  discrim_vocal_mpd = MultiPeriodDiscriminator().to(device)
  discrim_whole_msd = MultiScaleDiscriminator().to(device)
  discrim_vocal_msd = MultiScaleDiscriminator().to(device)

  print('Built networks')
  #Load saved dicts
  if os.path.exists(gen_speech2sing_save_path):
    gen_speech2sing.load_state_dict(torch.load(gen_speech2sing_save_path, map_location=device))
    print('Loaded gen_speech2sing saved parameters')
  if os.path.exists(gen_sing2speech_save_path):
    gen_sing2speech.load_state_dict(torch.load(gen_sing2speech_save_path, map_location=device))
    print('Loaded gen_sing2speech saved parameters')
  if os.path.exists(gen_preprocess_singing_save_path):
    gen_preprocess_singing.load_state_dict(torch.load(gen_preprocess_singing_save_path, map_location=device))
    print('Loaded gen_preprocess_singing saved parameters')
  if os.path.exists(discrim_whole_mpd_save_path):
    discrim_whole_mpd.load_state_dict(torch.load(discrim_whole_mpd_save_path, map_location=device))
    print('Loaded discrim_whole saved parameters')
  if os.path.exists(discrim_vocal_mpd_save_path):
    discrim_vocal_mpd.load_state_dict(torch.load(discrim_vocal_mpd_save_path, map_location=device))
    print('Loaded discrim_vocal saved parameters')
  if os.path.exists(discrim_whole_msd_save_path):
    discrim_whole_msd.load_state_dict(torch.load(discrim_whole_msd_save_path, map_location=device))
    print('Loaded discrim_whole saved parameters')
  if os.path.exists(discrim_vocal_msd_save_path):
    discrim_vocal_msd.load_state_dict(torch.load(discrim_vocal_msd_save_path, map_location=device))
    print('Loaded discrim_vocal saved parameters')

  opt_gen = torch.optim.Adam(itertools.chain(gen_speech2sing.parameters(),gen_sing2speech.parameters(),gen_preprocess_singing.parameters()), lr=hparams['learning_rate'],betas=(hparams['adam_b1'],hparams['adam_b2']))
  opt_disc = torch.optim.Adam(itertools.chain(discrim_whole_mpd.parameters(),discrim_vocal_mpd.parameters(),discrim_whole_msd.parameters(),discrim_vocal_msd.parameters()), lr=hparams['learning_rate'],betas=(hparams['adam_b1'],hparams['adam_b2']))

  return gen_speech2sing, gen_sing2speech, gen_preprocess_singing, discrim_whole_mpd, discrim_vocal_mpd, discrim_whole_msd, discrim_vocal_msd, [opt_gen,opt_disc]

#Set learning rate
def update_lr(lr,opt_gen,opt_disc):
  opt_gen.learning_rate = lr['gen']
  opt_disc.learning_rate = lr['disc']

# Train

In [ ]:
audio_duration = 2 #time of slice in seconds

In [ ]:
def get_song_pairs(root_dir):
    song_pairs = []
    for folder_name in os.listdir(root_dir):
        folder_path = os.path.join(root_dir, folder_name)
        if os.path.isdir(folder_path):
            voc_files = []
            acc_files = []
            for file_name in os.listdir(folder_path):
                if file_name.startswith('voc_') and file_name.endswith('.wav'):
                    voc_files.append(os.path.join(folder_path, file_name))
                elif file_name.startswith('acc_') and file_name.endswith('.wav'):
                    acc_files.append(os.path.join(folder_path, file_name))

            # Match voc and acc files based on index (assuming consistent naming)
            for voc_file in voc_files:
                base_name = os.path.basename(voc_file)
                index_str = base_name[4:-4]  # Extract index from "voc_1.wav"
                matching_acc_file = os.path.join(folder_path, f"acc_{index_str}.wav")
                if matching_acc_file in acc_files:
                  song_pairs.append((voc_file, matching_acc_file))

    return song_pairs

# Example usage
songs_root = os.path.join(dataset_path, f'songs_{audio_duration}s')
songs_pairs = get_song_pairs(songs_root)

# Print the pairs found len
len(songs_pairs)


45524

In [ ]:
def get_librispeech_paths(libri_speech_path):
  speech_paths = []
  for root, _, files in os.walk(libri_speech_path):
    #get the file that ends with .txt
    for file in files:
      file_path = os.path.join(root, file)
      speech_paths.append(file_path)
  return speech_paths


libri_speech_path = os.path.join(dataset_path, f'Librispeech_{audio_duration}s')
speech_paths = get_librispeech_paths(libri_speech_path)
len(speech_paths)

2703

In [ ]:
import random

class audio_dataset(torch.utils.data.Dataset):
  def __init__(self, songs_pairs, speech_paths):
    self.songs_pairs = songs_pairs
    self.speech_paths = speech_paths
  def __len__(self):
    return len(self.songs_pairs)

  def __getitem__(self, index):

    # get random file from songs_pairs and speech_paths
    song_pair = random.choice(self.songs_pairs)
    speech_path = random.choice(self.speech_paths)

    voc,sr = torchaudio.load(song_pair[0])
    acc, sr = torchaudio.load(song_pair[1])

    speech, sr = torchaudio.load(speech_path)

    # Convert to mel spectrogram
    mel_acc = convert_waveform_to_mel_spectrogram(acc).squeeze()
    mel_voc = convert_waveform_to_mel_spectrogram(voc).squeeze()
    mel_orig = combine_mel_spectrograms(mel_acc, mel_voc).squeeze()
    mel_speech = convert_waveform_to_mel_spectrogram(speech).squeeze()


    return mel_acc, mel_voc, mel_orig, mel_speech, voc, acc

In [ ]:
ds = audio_dataset(songs_pairs, speech_paths)

In [ ]:
dl = torch.utils.data.DataLoader(ds, batch_size=5, shuffle=True, num_workers = 2)

In [ ]:
# save_models()

In [ ]:
epochs = 2
gen_speech2sing, gen_sing2speech, gen_preprocess_singing, discrim_whole_mpd, discrim_vocal_mpd, discrim_whole_msd, discrim_vocal_msd, optimizers = get_networks(hparams)
# train(epochs, songs_batches, speech_batches, gen_speech2sing, gen_sing2speech, discrim_whole, discrim_vocal, optimizers)


/usr/local/lib/python3.11/dist-packages/torch/nn/utils/weight_norm.py:143: FutureWarning: `torch.nn.utils.weight_norm` is deprecated in favor of `torch.nn.utils.parametrizations.weight_norm`.
  WeightNorm.apply(module, name, dim)


Built networks


<ipython-input-30-fde99f6e3135>:16: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  gen_speech2sing.load_state_dict(torch.load(gen_speech2sing_save_path, map_location=device))

Loaded gen_speech2sing saved parameters


<ipython-input-30-fde99f6e3135>:19: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  gen_sing2speech.load_state_dict(torch.load(gen_sing2speech_save_path, map_location=device))

...

Loaded discrim_vocal saved parameters


<ipython-input-30-fde99f6e3135>:31: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  discrim_whole_msd.load_state_dict(torch.load(discrim_whole_msd_save_path, map_location=devi

Loaded discrim_whole saved parameters


<ipython-input-30-fde99f6e3135>:34: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  discrim_vocal_msd.load_state_dict(torch.load(discrim_vocal_msd_save_path, map_location=devi

Loaded discrim_vocal saved parameters


In [ ]:
import matplotlib.pyplot as plt
def display_spectrogram(spectrogram, title, ax, vmin, vmax, ylabel='freq_bin', aspect='auto', xmax=None):
  ax.set_title(title)
  ax.set_ylabel(ylabel)
  ax.set_xlabel('time-bins')
  im = ax.imshow(librosa.power_to_db(spectrogram), origin='lower', aspect=aspect, vmin=vmin, vmax=vmax)
  if xmax:
    ax.set_xlim((0, xmax))
  return im  # Return the image for colorbar


In [ ]:
import traceback

opt_gen, opt_disc = optimizers
for epoch in range(epochs):
    # Iterate over your dataset in batches
    batch_number = 0
    try:
      for batch in dl:
        print(f"Running batch {batch_number}")
        mel_accs, mel_vocs, mel_origs, mel_speeches, vocs, accs = batch
        # mel_accs = mel_accs.to(device)
        # mel_vocs = mel_vocs.to(device)
        # mel_origs = mel_origs.to(device)
        # mel_speeches = mel_speeches.to(device)

        # normalize all to 1
        mel_accs = mel_accs / torch.max(mel_accs)
        mel_vocs = mel_vocs / torch.max(mel_vocs)
        mel_origs = mel_origs / torch.max(mel_origs)
        vocs = vocs / torch.max(vocs)
        accs = accs / torch.max(accs)

        # Run Generators
        preprocess_vocals = gen_preprocess_singing(mel_vocs)
        preprocess_vocals = preprocess_vocals[:,:,:-(preprocess_vocals.shape[2]-accs.shape[2])]
        preprocess_vocals_spectrograms = torch.stack([convert_waveform_to_mel_spectrogram(preprocess_vocal).squeeze() for preprocess_vocal in preprocess_vocals])

        mel_sing_speech_combine = combine_mel_spectrograms(mel_speeches, preprocess_vocals_spectrograms)
        fake_vocs = gen_speech2sing(mel_sing_speech_combine)
        fake_vocs = fake_vocs[:,:,:-(fake_vocs.shape[2]-accs.shape[2])]
        fake_vocs = fake_vocs / torch.max(fake_vocs)
        fake_vocs_spectrogram = torch.stack([convert_waveform_to_mel_spectrogram(fake_voc).squeeze() for fake_voc in fake_vocs])
        fake_vocs_spectrogram = fake_vocs_spectrogram / torch.max(fake_vocs_spectrogram)

        voc_to_speech = gen_sing2speech(fake_vocs_spectrogram)
        voc_to_speech = voc_to_speech[:,:,:-(voc_to_speech.shape[2]-accs.shape[2])]
        voc_to_speech = voc_to_speech / torch.max(voc_to_speech)
        voc_to_speech_spectrogram = torch.stack([convert_waveform_to_mel_spectrogram(voc_to_speech).squeeze() for voc_to_speech in voc_to_speech])
        voc_to_speech_spectrogram = voc_to_speech_spectrogram / torch.max(voc_to_speech_spectrogram)

        fake_combine = fake_vocs + accs
        origs_combine = vocs + accs
        # Run Discriminators
        whole_real_output_mpd, whole_fake_output_mpd, _, _ = discrim_whole_mpd(origs_combine.detach(), fake_combine.detach())
        whole_real_output_msd, whole_fake_output_msd, _, _ = discrim_whole_msd(origs_combine.detach(), fake_combine.detach())

        vocal_real_output_mpd, vocal_fake_output_mpd, _, _ = discrim_vocal_mpd(vocs.detach(), fake_vocs.detach())
        vocal_real_output_msd, vocal_fake_output_msd, _, _ = discrim_vocal_msd(vocs.detach(), fake_vocs.detach())

        # Train discriminators
        opt_disc.zero_grad()
        d_loss_whole = discriminator_loss(whole_real_output_mpd, whole_fake_output_mpd) + discriminator_loss(whole_real_output_msd, whole_fake_output_msd)
        d_loss_vocal = discriminator_loss(vocal_real_output_mpd, vocal_fake_output_mpd) + discriminator_loss(vocal_real_output_msd, vocal_fake_output_msd)
        d_loss = d_loss_whole + d_loss_vocal
        d_loss.backward()
        opt_disc.step()
        print(f"d_loss: {d_loss.item()}; built of 'd_loss_whole:{d_loss_whole.item()}' & 'd_loss_vocal':{d_loss_vocal.item()}")

        #Train generators
        opt_gen.zero_grad()
        # whole_features_real_mpd, whole_features_fake_mpd output may need to be define in another way
        whole_real_output_mpd, whole_fake_output_mpd, whole_features_real_mpd, whole_features_fake_mpd = discrim_whole_mpd(origs_combine.detach(), fake_combine.detach())
        whole_real_output_msd, whole_fake_output_msd, whole_features_real_msd, whole_features_fake_msd = discrim_whole_msd(origs_combine.detach(), fake_combine.detach())

        vocal_real_output_mpd, vocal_fake_output_mpd, _, _ = discrim_vocal_mpd(vocs.detach(), fake_vocs.detach())
        vocal_real_output_msd, vocal_fake_output_msd, _, _ = discrim_vocal_msd(vocs.detach(), fake_vocs.detach())

        # whole_features_loss_mpd = feature_loss(whole_features_real_mpd, whole_features_fake_mpd)
        # whole_features_loss_msd = feature_loss(whole_features_real_msd, whole_features_fake_msd)
        g_loss_mpd_msd = generator_loss(whole_fake_output_mpd) + generator_loss(whole_fake_output_msd) + generator_loss(vocal_fake_output_mpd) + generator_loss(vocal_fake_output_msd)

        mae_loss_speech = mae(voc_to_speech_spectrogram, mel_speeches)
        g_loss = g_loss_mpd_msd + mae_loss_speech
        g_loss.backward()
        opt_gen.step()
        print(f"g_loss: {g_loss.item()}; built of g_loss_mpd_msd:{g_loss_mpd_msd.item()} & 'mae_loss_speech:{mae_loss_speech.item()}'") #& 'whole_features_loss_mpd:{whole_features_loss_mpd.item()}' & 'whole_features_loss_msd:{whole_features_loss_msd.item()}'")

        if batch_number % 100 == 0:
          try:
            print("generated singing:")
            ipd.display(ipd.Audio(fake_vocs[0].detach().numpy(), rate=sr))
            print("song original singing:")
            ipd.display(ipd.Audio(vocs[0].detach().numpy(), rate=sr))
            print("generated speech:")
            ipd.display(ipd.Audio(voc_to_speech[0].detach().numpy(), rate=sr))
            print("original speech")
            reconstructed_audio_speech = GRAD(mel_speeches[0].detach(), mel_transform)
            ipd.display(ipd.Audio(reconstructed_audio_speech.numpy(), rate=sr))
            print("original speech and background")
            reconstructed_audio_orig = GRAD(mel_sing_speech_combine[0].detach(), mel_transform)
            ipd.display(ipd.Audio(reconstructed_audio_orig.numpy(), rate=sr))
            # print("original accompinemant")
            # reconstructed_audio_acc = GRAD(mel_accs[0].detach(), mel_transform)
            # ipd.display(ipd.Audio(reconstructed_audio_acc.numpy(), rate=sr))

            # plt.show()
            save_models(gen_speech2sing, gen_sing2speech, gen_preprocess_singing, discrim_whole_mpd, discrim_vocal_mpd, discrim_whole_msd, discrim_vocal_msd)

          except Exception as e:
              print(f"Error Saving: {e}")
              traceback.print_exc()
        batch_number += 1

    except Exception as e:
        print(f"Error during training: {e}")
        traceback.print_exc()

    # print(f"Models saved for epoch {epoch + 1} in {save_path}")

Running batch 0
d_loss: 2.005423069000244; built of 'd_loss_whole:0.9995829463005066' & 'd_loss_vocal':1.0058401823043823
g_loss: 22.943035125732422; built of g_loss_mpd_msd:13.80732250213623 & 'mae_loss_speech:9.135713577270508'
generated singing:


song original singing:
generated speech:
original speech


  0%|          | 0/1000 [00:00<?, ?it/s]/usr/local/lib/python3.11/dist-packages/torch/nn/modules/loss.py:128: UserWarning: Using a target size (torch.Size([80, 130])) that is different to the input size (torch.Size([1, 80, 130])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.l1_loss(input, target, reduction=self.reduction)
100%|██████████| 1000/1000 [00:04<00:00, 218.94it/s, loss=0.266, spectral_convergence=-29.3]


original speech and background


100%|██████████| 1000/1000 [00:04<00:00, 205.67it/s, loss=0.246, spectral_convergence=-38.1]


...

original speech


100%|██████████| 1000/1000 [00:05<00:00, 196.19it/s, loss=0.389, spectral_convergence=-25.9]


original speech and background


100%|██████████| 1000/1000 [00:05<00:00, 197.14it/s, loss=0.616, spectral_convergence=-24]


Running batch 1101
d_loss: 0.01030239649116993; built of 'd_loss_whole:0.00923830270767212' & 'd_loss_vocal':0.0010640938999131322
g_loss: 29.019275665283203; built of g_loss_mpd_msd:15.960235595703125 & 'mae_loss_speech:13.059041023254395'
Running batch 1102
d_loss: 0.017468107864260674; built of 'd_loss_whole:0.016149867326021194' & 'd_loss_vocal':0.0013182410039007664
g_loss: 27.28687286376953; built of g_loss_mpd_msd:15.908647537231445 & 'mae_loss_speech:11.378226280212402'
Running batch 1103
d_loss: 0.03964382782578468; built of 'd_loss_whole:0.034941527992486954' & 'd_loss_vocal':0.004702300764620304
g_loss: 30.167360305786133; built of g_loss_mpd_msd:15.857013702392578 & 'mae_loss_speech:14.310346603393555'
Running batch 1104
d_loss: 0.04002070054411888; built of 'd_loss_whole:0.03766581788659096' & 'd_loss_vocal':0.0023548833560198545


In [ ]:
def convert_waveform_to_mel_spectrogram(waveform):
    # Convert waveform to Mel spectrogram
    padded_waveform = torch.nn.functional.pad(waveform, (0, n_fft - waveform.size(1) % hop_length))
    mel_spectrogram = mel_transform(padded_waveform)  # Shape: [1, n_mels, time_steps]
    return mel_spectrogram

In [ ]:
convert_waveform_to_mel_spectrogram(fake_vocs[0]).squeeze().shape

In [ ]:
convert_waveform_to_mel_spectrogram(vocs[0]).shape

In [ ]:
vocs.shape

In [ ]:
fake_vocs.shape

In [ ]:
fake_vocs[:,:,:-(fake_vocs.shape[2]-accs.shape[2])].shape

In [ ]:
ipd.display(ipd.Audio(fake_vocs[0].detach().numpy(), rate=sr))

In [ ]:
import matplotlib.pyplot as plt
print("generated singing:")
# reconstructed_audio = GRAD(fake_vocs[0].detach(), mel_transform)
# ipd.display(ipd.Audio(reconstructed_audio.numpy(), rate=sr))
# display fake_vocs[0] spectrogram image

# plt.imshow(fake_vocs[0].detach().numpy().squeeze(), aspect='auto', origin='lower', cmap='viridis')
# plt.colorbar(format='%+2.0f dB')
# plt.title('Mel Spectrogram')
# plt.xlabel('Time')
# plt.ylabel('Frequency')
# Assuming fake_vocs, mel_accs, mel_vocs, mel_speeches are defined
fig, axs = plt.subplots(1, 4, figsize=(20, 5), sharey=True)  # 1 row, 4 columns

# Plot spectrograms
im1 = display_spectrogram(fake_vocs[0].detach().numpy().squeeze(), title='Fake singing spectrogram', ax=axs[0])
im2 = display_spectrogram(mel_accs[0].detach().numpy().squeeze(), title='Acc', ax=axs[1])
im3 = display_spectrogram(mel_vocs[0].detach().numpy().squeeze(), title='Original singing spectrogram', ax=axs[2])
im4 = display_spectrogram(mel_speeches[0].detach().numpy().squeeze(), title='Original speech spectrogram', ax=axs[3])

# Add a single colorbar
fig.colorbar(im1, ax=axs, format='%+2.0f dB')  # Use any of the images for colorbar

plt.show()


# print("song original singing:")
# reconstructed_audio_voc = GRAD(mel_vocs[0].detach(), mel_transform)
# ipd.display(ipd.Audio(reconstructed_audio_voc.numpy(), rate=sr))
# print("generated speech:")
# reconstructed_audio_speech = GRAD(voc_to_speech[0].detach(), mel_transform)
# ipd.display(ipd.Audio(reconstructed_audio_speech.numpy(), rate=sr))
# print("original speech")
# reconstructed_audio_orig = GRAD(mel_speeches[0].detach(), mel_transform)
# ipd.display(ipd.Audio(reconstructed_audio_orig.numpy(), rate=sr))
# print("original accompinemant")
# reconstructed_audio_acc = GRAD(mel_accs[0].detach(), mel_transform)
# ipd.display(ipd.Audio(reconstructed_audio_acc.numpy(), rate=sr))
# save_models(gen_speech2sing, gen_sing2speech, discrim_whole, discrim_vocal)